In [1]:
from pdfminer.high_level import extract_pages
from pdfminer.layout import LTTextContainer, LTTextLine, LTChar
from pypdf import PdfReader
import re

# ***Tạo hàm xử lý các chunk***

In [2]:
# Xác định format của chunk được sử dụng:

# {
#   "id": "3-2-1",
#   "values": [0.123, -0.456, ...],
#   "metadata": {
#     "subject": "Lịch sử ĐCSVN",
#     "chapter": "Chương III",
#     "chapter_title": "Chương III: Đường lối kháng chiến",
#     "section": "II.",
#     "section_title": "II. Giai đoạn đầu",
#     "subsection": "1.",
#     "subsection_title": "1. Tư tưởng chỉ đạo",
#     "content": "...",
#     "position_in_document": 73,
#     "tokens": 296,
#     "type": "theory"
#   }
# }

In [3]:
def parse_chapters(text):
    """
    Phân tích 1 dòng chương/tiêu đề, hỗ trợ các định dạng:
    - 'Chương 1 Tiêu đề...'
    - 'Chương nhập môn Tiêu đề...'
    - 'I. Tiêu đề...'
    - '1. Tiêu đề...'

    Trả về tuple: (chapter_number, chapter_title)
    Nếu không khớp format, trả về (None, None)
    """
    pattern = re.compile(
        r"""^\s*
        (                                         # Nhóm 1: định danh chương
            Chương\s+(?:nhập\s+môn|\d+)           # 'Chương nhập môn' hoặc 'Chương <số>'
            |[IVXLCDM]+\.                         # Số La Mã có dấu chấm (I., II., ...)
            |\d+\.?                                # Số thường, có thể có hoặc không dấu chấm
        )
        \s*(.*)                                    # Nhóm 2: tiêu đề còn lại
        """, re.IGNORECASE | re.VERBOSE
    )
    
    line = text.strip()
    match = pattern.match(line)
    if match:
        chapter_number = match.group(1).strip().rstrip('.') or "None"
        chapter_title = match.group(2).strip() or "None"

        if (chapter_number and len(chapter_number) > 1) or (chapter_title and len(chapter_title) > 1):
            return chapter_number, chapter_title
        else:
            return "None", text
    else:
        return "None", text


In [4]:
chapter_number, chapter_title = parse_chapters('KẾT LUẬN')
print(chapter_number)
print(chapter_title)

None
KẾT LUẬN


In [5]:
import unicodedata
import re

def normalize_text(text):
    """
    Chuyển chuỗi thành lowercase, xóa dấu, và xóa toàn bộ khoảng trắng.
    """
    # Lowercase
    text = text.lower()

    # Bỏ dấu
    text = unicodedata.normalize('NFD', text)
    text = ''.join(c for c in text if unicodedata.category(c) != 'Mn')

    # Xóa toàn bộ khoảng trắng (space, tab, newline)
    text = re.sub(r'\s+', '', text)

    return text

# ***Gọi mô hình embed***

In [6]:
from sentence_transformers import SentenceTransformer
import torch

embedding_model = SentenceTransformer("AITeamVN/Vietnamese_Embedding")
embedding_model.max_seq_length = 2048

# embed = embedding_model.encode("Xin chao ban")

C:\Users\Duongw\AppData\Roaming\Python\Python313\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [29]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
def split_chunk_langchain(
    chapter_line,
    section_line,
    sub_section_line,
    content_line,
    max_chars=2048,
    model=None
):

    splitter = RecursiveCharacterTextSplitter(
        chunk_size=max_chars,
        chunk_overlap=300,  
        separators=["\n\n", "\n", ".", " ", ""]
    )
    content_chunks = splitter.split_text(content_line)

    # Xử lý metadata như cũ
    chapter_number, chapter_title = parse_chapters(chapter_line) if chapter_line else ("None", "None")
    section_number, section_title = parse_chapters(section_line) if section_line else ("None", "None")
    subsection_number, subsection_title = parse_chapters(sub_section_line) if sub_section_line else ("None", "None")

    if 'MỤC TIÊU' in section_line:
        chunk_type = 'TARGET'
    elif 'NỘI DUNG ÔN TẬP VÀ THẢO LUẬN' in section_line:
        chunk_type = 'EXERCISES'
    else:
        chunk_type = 'THEORY'

    result = []
    for i, content_piece in enumerate(content_chunks):
        content = content_piece.strip()
        chunk = {
            "id": f"LSD_{normalize_text(chapter_number) if chapter_number else 0}_{section_number if section_number else 0}_{subsection_number if subsection_number else 0}_{i}",
            "values": model.encode(content).tolist(),
            "metadata": {
                "subject": "Lịch sử Đảng Cộng Sản Việt Nam",
                "chapter": chapter_number,
                "chapter_title": chapter_title,
                "section": section_number,
                "section_title": section_title,
                "subsection": subsection_number,
                "subsection_title": subsection_title,
                "content": content,
                "tokens": len(content_piece),
                "type": chunk_type
            }
        }
        result.append(chunk)

    return result

In [64]:
import numpy as np

def bm25_tokenize(text):
    return text.lower().split()

def text_to_sparse_vector_bm25(text, bm25, vocabulary):
    tokens = bm25_tokenize(text)
    vector = np.zeros(len(vocabulary))
    for i, word in enumerate(vocabulary):
        idf = bm25.idf.get(word, 0)
        tf = tokens.count(word)
        vector[i] = idf * tf
    indices = vector.nonzero()[0].tolist()
    values = vector[indices].tolist()
    return {"indices": indices, "values": values}

def split_chunk_langchain_sparse(
    chapter_line,
    section_line,
    sub_section_line,
    content_line,
    bm25=None,
    vocabulary=None,
    max_chars=2048
):
    splitter = RecursiveCharacterTextSplitter(
        chunk_size=max_chars,
        chunk_overlap=300,
        separators=["\n\n", "\n", ".", " ", ""]
    )
    content_chunks = splitter.split_text(content_line)

    # Metadata parsing
    chapter_number, chapter_title = parse_chapters(chapter_line) if chapter_line else ("None", "None")
    section_number, section_title = parse_chapters(section_line) if section_line else ("None", "None")
    subsection_number, subsection_title = parse_chapters(sub_section_line) if sub_section_line else ("None", "None")

    if 'MỤC TIÊU' in section_line:
        chunk_type = 'TARGET'
    elif 'NỘI DUNG ÔN TẬP VÀ THẢO LUẬN' in section_line:
        chunk_type = 'EXERCISES'
    else:
        chunk_type = 'THEORY'

    result = []
    for i, content_piece in enumerate(content_chunks):
        content = content_piece.strip()
        sparse_vector = text_to_sparse_vector_bm25(content, bm25, vocabulary)

        chunk = {
            "id": f"LSD_{normalize_text(chapter_number) if chapter_number else 0}_{section_number if section_number else 0}_{subsection_number if subsection_number else 0}_{i}",
            "sparse_values": sparse_vector,
            "metadata": {
                "subject": "Lịch sử Đảng Cộng Sản Việt Nam",
                "chapter": chapter_number,
                "chapter_title": chapter_title,
                "section": section_number,
                "section_title": section_title,
                "subsection": subsection_number,
                "subsection_title": subsection_title,
                "content": content,
                "tokens": len(content_piece),
                "type": chunk_type
            }
        }
        result.append(chunk)

    return result


# ***Chunk văn bản***

In [8]:
pdf_path = "gt-lich-su-dang-csvn-ban-tuyen-giao-tw.pdf"

#Tạo fulltext để chứa toàn bộ các dòng chử trong file Lịch sử Đảng
sections = []

# Lấy số trang trong file PDF
reader = PdfReader(pdf_path)
total_pages = len(reader.pages)
print("Số trang trong PDF:", total_pages)

Số trang trong PDF: 219


In [9]:
def chunking_LSD_test(pdf_path):
    '''
        Hàm được sử dụng để chunk tài liệu lịch sử đảng theo từng chương, tiêu đề mục, mục con.
        Các tham số:
            - pdf_path: đường dẫn đến file pdf của môn Lịch sử đảng
            - chunk_list: Chứa các chunk đã được xử lý
        
        Hàm sẽ trả về danh sách chứa các chunk của môn LSD
    '''

    chunk_list = []
    is_content = False

    curr_chapter_line = ""
    curr_section_line = ""
    curr_sub_section_line = ""
    curr_content_line = ""
    count = 0
    #Duyệt qua từng trang trong file pdf, bắt đầu từ trang 2 (bỏ qua trang bìa)
    for page_layout in extract_pages(pdf_path, page_numbers=range(2, total_pages)):
        #Duyệt qua từng phần tử trong trang
        for element in page_layout:
            if isinstance(element, LTTextContainer):

                # Duyet qua từng dòng chữ trong phần tử
                for text_line in element:
                    if isinstance(text_line, LTTextLine):
                        
                        #Lấy ra từng kí tự bên trong dòng chữ
                        for obj in text_line:
                            if isinstance(obj, LTChar):
                                '''
                                Dựa vào kích thước chữ để phân loại các phần trong tài liệu
                                - Kích thước chữ = 14: Chương và tiêu đề của chương - Done
                                - Kích thước chữ = 13, vừa in đậm vừa in nghiêng: Tiêu đề phụ (1 nhỏ, 2 nhỏ, 3 nhỏ, ...) - Done
                                - Kích thước chữ = 13, chỉ in đậm không in nghiêng: Tiêu đề lớn ( 1 la mã, 2 la mã, 3 la mã, ...), Mục Tiêu ( Chú ý xử lý trường hợp này) - Done
                                - Kích thước chữ > 12.9: Các nội dung chính
                                - Kích thước chữ = 12: Số trang - Done
                                - Kích thước chữ < 11: Nội dung phụ, chú thích, ghi chú (Loại bỏ các trường hợp này) - Done
                                '''
                                #Lấy ra thông tin của kí tự
                                font = obj.fontname
                                text = obj.get_text()
                                text_size = obj.size

                                if text_size == 14:    #Lấy ra các ký tự có kích thước chữ = 14, đây là tiêu đề chương
                                    #Nếu có nội dung chương trước đó thì đẩy 1 chunk
                                    if is_content == True:
                                        chunk = split_chunk_langchain(curr_chapter_line, curr_section_line, curr_sub_section_line, curr_content_line, max_chars=2048, model=embedding_model)
                                        chunk_list.extend(chunk)
                                        curr_chapter_line = ""
                                        curr_section_line = ""
                                        curr_sub_section_line = ""
                                        curr_content_line = ""
                                        is_content = False

                                    # curr_chapter_line =""
                                    curr_chapter_line += text

                                elif text_size > 12.9 and text_size < 14:   #Lấy ra các ký tự có kích thước chữ > 12.9 (Đây là nội dung chính)

                                    #Tiêu đề la mã
                                    if ("Bold" in font) and ("Italic" not in font):
                                        #Nếu có nội dung chương trước đó thì đẩy 1 chunk
                                        if is_content == True and text != " " and text != "c" and text != ",":
                                            if "KẾT LUẬN" in curr_section_line:
                                                curr_chapter_line = "KẾT LUẬN"
                                                curr_section_line = ""
                                                curr_sub_section_line = ""
                                            chunk = split_chunk_langchain(curr_chapter_line, curr_section_line, curr_sub_section_line, curr_content_line, max_chars=2048, model=embedding_model)
                                            chunk_list.extend(chunk)
                                            curr_section_line = ""
                                            curr_sub_section_line = ""
                                            curr_content_line = ""

                                            is_content = False

                                        # curr_section_line = ""
                                        curr_section_line += text
                                    
                                    #Tiêu đề phụ
                                    elif ("Italic" in font) and ("Bold" in font):
                                        #Nếu có nội dung chương trước đó thì đẩy 1 chunk
                                        if is_content == True and text != " ":
                                            chunk = split_chunk_langchain(curr_chapter_line, curr_section_line, curr_sub_section_line, curr_content_line, max_chars=2048, model=embedding_model)
                                            chunk_list.extend(chunk)
                                            curr_sub_section_line = ""
                                            curr_content_line = ""
                                            is_content = False

                                        # curr_sub_section_line =""
                                        curr_sub_section_line += text
                                    
                                    #Trường hợp là văn bản bình thường
                                    else:
                                        is_content = True
                                        curr_content_line += text
                    if curr_content_line != "":
                        curr_sub_section_line += " "
                    if curr_chapter_line != "":
                        curr_chapter_line += " "
                    if curr_section_line != "":
                        curr_section_line += " "
                    if curr_sub_section_line != "":
                        curr_sub_section_line += " "
    return chunk_list

In [18]:
def extract_raw_chunks_LSD(pdf_path, total_pages):
    """
    Trích xuất các đoạn nội dung theo chương - mục - mục con mà chưa split theo embedding.
    Trả về danh sách các dict: {"chapter": ..., "section": ..., "sub_section": ..., "content": ...}
    """
    raw_chunks = []
    is_content = False

    curr_chapter_line = ""
    curr_section_line = ""
    curr_sub_section_line = ""
    curr_content_line = ""
    temp = ["1", "2", "3", "4"]
    count = 0 
    for page_layout in extract_pages(pdf_path, page_numbers=range(2, total_pages)):
        for element in page_layout:
            if isinstance(element, LTTextContainer):
                for text_line in element:
                    if isinstance(text_line, LTTextLine):
                        line_text = ""
                        for obj in text_line:
                            if isinstance(obj, LTChar):
                                char = obj.get_text()
                                size = obj.size

                                if size < 10 and char.isdigit():
                                    continue

                                line_text += char
                        line_text = line_text.strip()
                        # line_text = text_line.get_text().strip()
                        first_obj = next(iter(text_line), None)

                        if isinstance(first_obj, LTChar):
                            font = first_obj.fontname
                            text_size = first_obj.size

                            if text_size == 14:
                                if is_content:
                                    raw_chunks.append({
                                        "chapter": curr_chapter_line.strip(),
                                        "section": curr_section_line.strip(),
                                        "sub_section": curr_sub_section_line.strip(),
                                        "content": curr_content_line.strip()
                                    })
                                    curr_chapter_line = ""
                                    curr_section_line = ""
                                    curr_sub_section_line = ""
                                    curr_content_line = ""
                                    is_content = False
                                curr_chapter_line += line_text + " "

                            elif 12.9 < text_size < 14:
                                if "Bold" in font and "Italic" not in font:
                                    if is_content and line_text not in ["", " ", "c", ","]:
                                        for temp_item in temp:
                                            if temp_item in curr_section_line:
                                                curr_content_line = curr_section_line + curr_content_line
                                                curr_section_line = temp_item
                                                curr_sub_section_line = ""
                                        if "KẾT LUẬN" in curr_section_line.upper():
                                            curr_chapter_line = "KẾT LUẬN"
                                            curr_section_line = ""
                                            curr_sub_section_line = ""
                                        raw_chunks.append({
                                            "chapter": curr_chapter_line.strip(),
                                            "section": curr_section_line.strip(),
                                            "sub_section": curr_sub_section_line.strip(),
                                            "content": curr_content_line.strip()
                                        })
                                        curr_section_line = ""
                                        curr_sub_section_line = ""
                                        curr_content_line = ""
                                        is_content = False
                                    curr_section_line += line_text + " "

                                elif "Bold" in font and "Italic" in font:
                                    if is_content and line_text.strip() != "":
                                        raw_chunks.append({
                                            "chapter": curr_chapter_line.strip(),
                                            "section": curr_section_line.strip(),
                                            "sub_section": curr_sub_section_line.strip(),
                                            "content": curr_content_line.strip()
                                        })
                                        curr_sub_section_line = ""
                                        curr_content_line = ""
                                        is_content = False
                                    curr_sub_section_line += line_text + " "

                                else:
                                    is_content = True
                                    curr_content_line += line_text + " "
    if is_content and curr_content_line.strip():
        raw_chunks.append({
            "chapter": curr_chapter_line.strip(),
            "section": curr_section_line.strip(),
            "sub_section": curr_sub_section_line.strip(),
            "content": curr_content_line.strip()
        })

    return raw_chunks

In [19]:
raw_chunk = extract_raw_chunks_LSD(pdf_path, total_pages)

In [23]:
raw_chunk[:10]

[{'chapter': 'Chương nhập môn ĐỐI TƯỢNG, CHỨC NĂNG, NHIỆM VỤ, NỘI DUNG VÀ PHƯƠNG PHÁP NGHIÊN CỨU, HỌC TẬP LỊCH SỬ ĐẢNG CỘNG SẢN VIỆT NAM',
  'section': '',
  'sub_section': '',
  'content': 'Đảng Cộng sản Việt Nam do Chủ tịch Hồ Chí Minh sáng lập (3-2-1930). Từ thời điểm lịch sử đó, lịch sử của Đảng hòa quyện cùng lịch sử của dân tộc Việt Nam. Đảng đã lãnh đạo và đưa sự nghiệp cách mạng của giai cấp công nhân và dân tộc Việt Nam đi từ thắng lợi này đến thắng lợi khác, “có được cơ đồ là vị thế như ngày nay”. “Đảng Cộng sản Việt Nam là đội tiền phong của giai cấp công nhân, đồng thời là đội tiền phong của nhân dân lao động và của dân tộc Việt Nam, đại biểu trung thành lợi ích của giai cấp công nhân, nhân dân lao động và của dân tộc. Đảng lấy chủ nghĩa Mác-Lênin và tư tưởng Hồ Chí Minh làm nền tảng tư tưởng, kim chỉ nam cho hành động, lấy tập trung dân chủ làm nguyên tắc tổ chức cơ bản”. Lịch sử Đảng Cộng sản Việt Nam là một chuyên ngành, một bộ phận của khoa học lịch sử. Chuyên ngành lịc

In [65]:
from rank_bm25 import BM25Okapi

# Tạo corpus
corpus_texts = [chunk["content"] for chunk in raw_chunk]
tokenized_corpus = [bm25_tokenize(text) for text in corpus_texts]

bm25 = BM25Okapi(tokenized_corpus)
vocabulary = list(bm25.idf.keys())

In [20]:
def chunk_with_embedding(raw_chunks, embedding_model):
    """
    Nhận vào danh sách raw_chunks, sau đó gọi hàm split_chunk_langchain để xử lý nhỏ ra và thêm embedding nếu cần.
    """
    final_chunks = []
    for chunk in raw_chunks:
        split_chunks = split_chunk_langchain(
            chunk['chapter'],
            chunk['section'],
            chunk['sub_section'],
            chunk['content'],
            max_chars=2048,
            model=embedding_model
        )
        final_chunks.extend(split_chunks)

    return final_chunks

In [66]:
def chunk_with_embedding_sparse(raw_chunks):
    """
    Nhận vào danh sách raw_chunks, sau đó gọi hàm split_chunk_langchain để xử lý nhỏ ra và thêm embedding nếu cần.
    """
    final_chunks = []
    for chunk in raw_chunks:
        split_chunks = split_chunk_langchain_sparse(
            chunk['chapter'],
            chunk['section'],
            chunk['sub_section'],
            chunk['content'],
            bm25=bm25,
            vocabulary=vocabulary
        )
        final_chunks.extend(split_chunks)

    return final_chunks

In [67]:
LSD_BM25_chunk_list = chunk_with_embedding_sparse(raw_chunk)

In [68]:
LSD_BM25_chunk_list

[{'id': 'LSD_chuongnhapmon_None_None_0',
  'sparse_values': {'indices': [0,
    1,
    2,
    3,
    4,
    5,
    6,
    7,
    8,
    9,
    10,
    11,
    12,
    13,
    14,
    15,
    16,
    17,
    18,
    19,
    20,
    21,
    22,
    23,
    24,
    25,
    26,
    27,
    28,
    29,
    30,
    31,
    32,
    33,
    34,
    35,
    36,
    37,
    38,
    39,
    40,
    41,
    42,
    43,
    44,
    45,
    46,
    47,
    48,
    49,
    50,
    51,
    52,
    53,
    54,
    55,
    56,
    57,
    58,
    59,
    60,
    61,
    62,
    63,
    64,
    65,
    66,
    67,
    68,
    69,
    70,
    71,
    72,
    73,
    74,
    75,
    76,
    77,
    78,
    79,
    80,
    81,
    82,
    83,
    84,
    85,
    87,
    88,
    89,
    90,
    91,
    92,
    93,
    94,
    95,
    96,
    97,
    98,
    99,
    100,
    101,
    102,
    103,
    104,
    105,
    106,
    107,
    108,
    109,
    110,
    111,
    112,
    113,
    114,
    115,
    1

In [21]:
LSD_chunk_list = chunk_with_embedding(raw_chunk, embedding_model)

In [24]:
LSD_chunk_list[:10]

[{'id': 'LSD_chuongnhapmon_None_None_0',
  'values': [-0.014953368343412876,
   -0.053266700357198715,
   -0.034736812114715576,
   0.03202781826257706,
   0.012464629486203194,
   -0.013635995797812939,
   -0.04147278144955635,
   0.010536900721490383,
   0.008320667780935764,
   0.012044292874634266,
   0.032067812979221344,
   -0.009272487834095955,
   -0.004291944671422243,
   0.037977635860443115,
   0.00015704093675594777,
   -0.022527042776346207,
   -0.006381711456924677,
   -0.0544213242828846,
   0.004824823699891567,
   0.012655329890549183,
   0.020267121493816376,
   -0.030457518994808197,
   0.010849831625819206,
   0.0583307258784771,
   -0.004592837765812874,
   -0.03081151470541954,
   -0.012058952823281288,
   0.01022787019610405,
   0.0021935582626610994,
   -0.0048987180925905704,
   -0.013178662396967411,
   -0.04819966480135918,
   0.013019419275224209,
   0.034363627433776855,
   -0.004390059504657984,
   -0.009864091873168945,
   -0.0312002282589674,
   0.000449

# ***Lưu json ra ngoài***

In [69]:
import json
import os

def save_chunks_to_json(chunks, output_path):
    """
    Lưu danh sách các chunk (list of dict) ra file JSON.
    """
    os.makedirs(os.path.dirname(output_path), exist_ok=True)  # Tạo folder nếu chưa có

    with open(output_path, "w", encoding="utf-8") as f:
        json.dump(chunks, f, ensure_ascii=False, indent=2)

    print(f"✅ Đã lưu {len(chunks)} chunks vào: {output_path}")

In [70]:
output_path = r"./Lich_Su_Dang_Sparse.json"
save_chunks_to_json(LSD_BM25_chunk_list, output_path)

✅ Đã lưu 347 chunks vào: ./Lich_Su_Dang_Sparse.json


In [26]:
output_path = r"./Lich_Su_Dang.json"
save_chunks_to_json(LSD_chunk_list, output_path)

✅ Đã lưu 347 chunks vào: ./Lich_Su_Dang.json


In [27]:
output_path = r"./Lich_Su_Dang_raw.json"
save_chunks_to_json(raw_chunk, output_path)

✅ Đã lưu 50 chunks vào: ./Lich_Su_Dang_raw.json


# ***Upsert data lên database***


In [ ]:
# Đọc data từ file json
def load_chunks_from_json(file_path):
    with open(file_path, "r", encoding="utf-8") as f:
        chunks = json.load(f)
    return chunks

In [ ]:
LSD_chunk_list = load_chunks_from_json(r'./Lich_Su_Dang.json')

## ***Upsert dense vector***

In [ ]:
from pinecone.grpc import PineconeGRPC as Pinecone

pc = Pinecone(api_key=".")

# To get the unique host for an index, 
# see https://docs.pinecone.io/guides/manage-data/target-an-index
index = pc.Index(host="https://rag-ktcn-0abpzwm.svc.aped-4627-b74a.pinecone.io")

index.upsert(
  vectors=LSD_chunk_list,
  namespace="lich-su-dang"
)

upserted_count: 347

In [ ]:
from pinecone.grpc import PineconeGRPC as Pinecone

pc = Pinecone(api_key=".")

# To get the unique host for an index, 
# see https://docs.pinecone.io/guides/manage-data/target-an-index
index = pc.Index(host="https://ktcn-rag-sparse-0abpzwm.svc.aped-4627-b74a.pinecone.io")

index.upsert(
  vectors=LSD_BM25_chunk_list,
  namespace="lich-su-dang"
)

upserted_count: 347

## ***Upsert sparse vector***

In [ ]:
ques = embedding_model.encode("Chuẩn bị về tư tưởng, chính trị và tổ chức cho sự ra đời của Đảng")
print(ques)

[ 0.04104054 -0.00510341  0.01285447 ...  0.04795794  0.051929
 -0.02497853]


In [ ]:
for i, val in enumerate(ques):
    print(f"{val},")

0.041040536016225815,
-0.0051034074276685715,
0.012854472734034061,
0.040061891078948975,
-0.038181427866220474,
-0.0526052825152874,
-0.003456118982285261,
0.03069249354302883,
0.031958747655153275,
0.002948937239125371,
-0.014833729714155197,
-0.031448185443878174,
0.0101684695109725,
0.014891069382429123,
2.187215068261139e-05,
-0.011137526482343674,
0.03129482641816139,
0.008801590651273727,
0.04750143736600876,
0.019402360543608665,
0.023066435009241104,
0.016463562846183777,
0.023712212219834328,
0.04680332913994789,
-0.034665703773498535,
-0.01853039301931858,
0.007078604772686958,
-0.017771665006875992,
0.05547406151890755,
-0.009056346490979195,
-0.032206982374191284,
-0.04074594005942345,
-0.001665207906626165,
0.025421252474188805,
0.05840596184134483,
-0.02747529000043869,
-0.045693669468164444,
0.03473823517560959,
-0.03872450068593025,
-0.011260468512773514,
-0.013682530261576176,
0.01061213854700327,
-0.033130887895822525,
0.008762450888752937,
-0.008098769001662731,
-0.